<a href="https://colab.research.google.com/github/HannahShaw21/ST-554-Project1/blob/main/Task3/Project_1_Task_3_Hannah_Shaw.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Project 1 - On Field Calibration of Electronic Nose for Benzene Estimation

## Introduction

The dataset `air_quality` contains the responses of a gas multisensor device deployed on the field in an Italian city. Hourly responses averages are recorded along with gas concentrations references for CO, Non Metanic Hydrocarbons, Benzene, Total Nitrogen Oxides (NOx) and Nitrogen Dioxide (NO2) from a certified analyzer. Missing values are tagged with -200 value.

For this task, we want to evaluate if a simple linear regression (SLR) model using carbon monoxide concentrations (CO(GT)) or a multiple linear regression (MLR) model using CO(GT), temperature (T), relative humidity (RH), and absolute humidity (AH) is better at predicting benzene concentrations (C6H6(GT)).

# Task 3:

This task involves coding up a cross-validation algorithm to evaluate multiple linear regression models in the time series setting.

First, we will import the data, while carrying over the data cleaning/modifications from previous tasks.

In [51]:
# import Colab base imports
from pprint import pprint
from IPython.display import HTML, display, Markdown
import pandas as pd
import numpy as np
from datetime import date, datetime
import matplotlib.pyplot as plt
from sklearn.ensemble import RandomForestRegressor

# Global Options
pd.set_option('display.max_colwidth', None)

# load pandas as data table for quality of life
from google.colab import data_table
data_table.enable_dataframe_formatter()

!pip install ucimlrepo

from ucimlrepo import fetch_ucirepo

# fetch dataset
air_quality = fetch_ucirepo(id=360)

# data (as pandas dataframes)
X = air_quality.data.features
y = air_quality.data.targets

# metadata
print(air_quality.metadata)

# variable information
print(air_quality.variables)

{'uci_id': 360, 'name': 'Air Quality', 'repository_url': 'https://archive.ics.uci.edu/dataset/360/air+quality', 'data_url': 'https://archive.ics.uci.edu/static/public/360/data.csv', 'abstract': 'Contains the responses of a gas multisensor device deployed on the field in an Italian city. Hourly responses averages are recorded along with gas concentrations references from a certified analyzer. ', 'area': 'Computer Science', 'tasks': ['Regression'], 'characteristics': ['Multivariate', 'Time-Series'], 'num_instances': 9358, 'num_features': 15, 'feature_types': ['Real'], 'demographics': [], 'target_col': None, 'index_col': None, 'has_missing_values': 'no', 'missing_values_symbol': None, 'year_of_dataset_creation': 2008, 'last_updated': 'Sun Mar 10 2024', 'dataset_doi': '10.24432/C59K5F', 'creators': ['Saverio Vito'], 'intro_paper': {'ID': 420, 'type': 'NATIVE', 'title': 'On field calibration of an electronic nose for benzene estimation in an urban pollution monitoring scenario', 'authors': 

## Additional Data Cleaning for Task 3

Two things:

• Remove any observations where the C6H6(GT), CO(GT), T, RH, or AH are -200 as these represent missing
values (which we'll ignore).

• Create a new version of the data with the five variables in the previous bullet along with the Date
variable.
  - The values of the five variables above should be their average across the given Date.

In [52]:
print(X) #X = air_quality.data.features

           Date      Time  CO(GT)  PT08.S1(CO)  NMHC(GT)  C6H6(GT)  \
0     3/10/2004  18:00:00     2.6         1360       150      11.9   
1     3/10/2004  19:00:00     2.0         1292       112       9.4   
2     3/10/2004  20:00:00     2.2         1402        88       9.0   
3     3/10/2004  21:00:00     2.2         1376        80       9.2   
4     3/10/2004  22:00:00     1.6         1272        51       6.5   
...         ...       ...     ...          ...       ...       ...   
9352   4/4/2005  10:00:00     3.1         1314      -200      13.5   
9353   4/4/2005  11:00:00     2.4         1163      -200      11.4   
9354   4/4/2005  12:00:00     2.4         1142      -200      12.4   
9355   4/4/2005  13:00:00     2.1         1003      -200       9.5   
9356   4/4/2005  14:00:00     2.2         1071      -200      11.9   

      PT08.S2(NMHC)  NOx(GT)  PT08.S3(NOx)  NO2(GT)  PT08.S4(NO2)  \
0              1046      166          1056      113          1692   
1               955  

In [53]:
#Remove any observations where the C6H6(GT), CO(GT), T, RH, or AH are -200
raw_air_quality = X
#raw_air_quality = raw_air_quality[("C6H6(GT)" != -200) & ("CO(GT)" != -200) & ("T" != -200) & ("RH" != -200) & ("AH" != -200)]
#raw_air_quality = raw_air_quality[(raw_air_quality.C6H6(GT) != -200) & (raw_air_quality.CO(GT) != -200) & (raw_air_quality.T != -200) & (raw_air_quality.RH != -200) & (raw_air_quality.AH != -200)]
raw_air_quality = raw_air_quality[(raw_air_quality["C6H6(GT)"] != -200) & (raw_air_quality["CO(GT)"] != -200) & (raw_air_quality["T"] != -200) & (raw_air_quality["RH"] != -200) & (raw_air_quality["RH"] != -200)]
raw_air_quality

Date      Time  CO(GT)  PT08.S1(CO)  NMHC(GT)  C6H6(GT)  \
0     3/10/2004  18:00:00     2.6         1360       150      11.9   
1     3/10/2004  19:00:00     2.0         1292       112       9.4   
2     3/10/2004  20:00:00     2.2         1402        88       9.0   
3     3/10/2004  21:00:00     2.2         1376        80       9.2   
4     3/10/2004  22:00:00     1.6         1272        51       6.5   
...         ...       ...     ...          ...       ...       ...   
9352   4/4/2005  10:00:00     3.1         1314      -200      13.5   
9353   4/4/2005  11:00:00     2.4         1163      -200      11.4   
9354   4/4/2005  12:00:00     2.4         1142      -200      12.4   
9355   4/4/2005  13:00:00     2.1         1003      -200       9.5   
9356   4/4/2005  14:00:00     2.2         1071      -200      11.9   

      PT08.S2(NMHC)  NOx(GT)  PT08.S3(NOx)  NO2(GT)  PT08.S4(NO2)  \
0              1046      166          1056      113          1692   
1               955      103          1174       92          1559   
2               939      131          1140      114          1555   
3               948      172          1092      122          1584   
4               836      131          1205      116          1490   
...             ...      ...           ...      ...           ...   
9352           1101      472           539      190          1374   
9353           1027      353           604      179          1264   
9354           1063      293           603      175          1241   
9355            961      235           702      156          1041   
9356           1047      265           654      168          1129   

      PT08.S5(O3)     T    RH      AH  
0            1268  13.6  48.9  0.7578  
1             972  13.3  47.7  0.7255  
2            1074  11.9  54.0  0.7502  
3            1203  11.0  60.0  0.7867  
4            1110  11.2  59.6  0.7888  
...           ...   ...   ...     ...  
9352         1729  21.9  29.3  0.7568  
9353         1269  24.3  23.7  0.7119  
9354         1092  26.9  18.3  0.6406  
9355          770  28.3  13.5  0.5139  
9356          816  28.5  13.1  0.5028  

[7344 rows x 15 columns]

This reduces the number of entries from 9357 to 7344.

In [54]:
# Select only the columns 'Date', 'C6H6(GT)', 'CO(GT)', 'T', 'RH', and 'AH' from raw_air_quality
air_quality_focus = raw_air_quality[['Date', 'C6H6(GT)', 'CO(GT)', 'T', 'RH', 'AH']]
#air_quality_focus
air_quality_focus.head()

Date  C6H6(GT)  CO(GT)     T    RH      AH
0  3/10/2004      11.9     2.6  13.6  48.9  0.7578
1  3/10/2004       9.4     2.0  13.3  47.7  0.7255
2  3/10/2004       9.0     2.2  11.9  54.0  0.7502
3  3/10/2004       9.2     2.2  11.0  60.0  0.7867
4  3/10/2004       6.5     1.6  11.2  59.6  0.7888

In [55]:
# Now group entries by Date and turn the values of the other five variables into their average across the given Date.
#air_quality_focus.groupby("Date").describe()
average_air_quality = air_quality_focus.groupby("Date").mean()
average_air_quality["Day"] = range(1, len(average_air_quality) + 1) #Creates a new Day variable in our table - this will be useful later on

average_air_quality

C6H6(GT)    CO(GT)          T         RH        AH  Day
Date                                                               
1/1/2005    7.313043  2.134783   6.813043  51.260870  0.501643    1
1/10/2005  13.463636  2.127273  13.377273  68.413636  1.044486    2
1/11/2005  13.779167  2.812500  12.779167  64.104167  0.941413    3
1/12/2005  15.817391  3.273913  12.021739  65.443478  0.904865    4
1/13/2005  12.495833  2.679167   9.991667  69.566667  0.847225    5
...              ...       ...        ...        ...       ...  ...
9/5/2004    5.712500  1.304167  29.204167  27.237500  1.057429  343
9/6/2004    6.278261  1.421739  26.752174  35.934783  1.219478  344
9/7/2004    9.700000  1.890909  27.618182  33.318182  1.154682  345
9/8/2004   17.016667  3.316667  27.966667  26.433333  0.965850  346
9/9/2004   13.541667  2.237500  28.525000  26.550000  0.964671  347

[347 rows x 6 columns]

## Two Models Under Consideration

We'll use two competing models:

• An SLR model using CO(GT) to predict C6H6(GT)

• An MLR model using CO(GT), T, RH, and AH to predict C6H6(GT)

If you'd like, feel free to fit the two models to the full data set (ignoring date and hour which we'll consider later).

### Cross-Validation
We want to see how well these two competing models do at predicting. However, we can't use the usual
cross-validation because our data is over time (Day or Date).
We don't want to ignore the fact that two days close to each other likely share some correlation/association
when fitting and evaluating the model.
Instead, what we want to do is train the model/judge it sequentially.

1. Use the first 250 days of data to fit the model. Use that model to predict the 251st day. Calculate the
MSE for that prediction.
2. Use the first 251 days of data to fit the model. Use that model to predict the 252nd day. Calculate
the MSE for that prediction.
3. Repeat until you predict for the last day.
4. Sum up the MSE values to get an overall MSE for the model!

Write a function to do the above given a particular `X`, `y`, and starting `Date` or `Day`.

In [64]:
#Load in the modules we will need
from sklearn import linear_model
from sklearn.model_selection import train_test_split, cross_validate
from sklearn.metrics import mean_squared_error
from sklearn.linear_model import LinearRegression, LassoCV, Lasso

Some guidelines and helpful hints:

• First write a function to get the MSE for one step of the above.
 - Have this function take in a data frame of predictors `X` (this will be used in the `.fit()` method of a `LinearRegression()` object), a 1D response `y`, and a `day` argument. The `day` argument will correspond to the last day or date that should be used in the training data.
 - Use the `day` argument to subset the data into a training `X` and `y` and a testing `X` and `y`. Have your training set include all days up to and including day and your test set just include the `day` + 1 row.
 - Do the model fitting on the training and predict on the test set. Return the mean squared error.

 That will act as a helper function for our function that find the CV error.

In [66]:
def mse_finder(X, y, day):
  #Split the data into training and testing sets, with day determining where to split
  X_train = X[:day]
  X_test = X[day:]
  y_train = y[:day]
  y_test = y[day:]

  test_model = LinearRegression().fit(X_train, y_train)
  model_pred = test_model.predict(X_test)
  return mean_squared_error(y_test, model_pred)

Now write a function to obtain the CV value over all the days (other than the initial training block of 250 days).
 - Have this function take in `X`, `y` (both as above), and a `day` argument
 - Initialize an MSE value at 0
 - Use a loop to iterate from the `day` (here day 250, but this leaves it up to the user to decide) to the final `day` in the data set minus 1 (use code to determine this rather than hardcoding a final day)
    * Within the loop, use the helper function defined previously along with augmented assignment to add the MSE as you go
 - Return the MSE

In [67]:
def cv_finder(X, y, day):
  total_mse = 0
  for i in range(day, len(y)-1):
    mse_found = mse_finder(X, y, i)
    # Add the result from mse_finder to our mse_value using augmented assignment
    total_mse += mse_found
  return total_mse

Now run your function using the SLR model. Repeat using the MLR model. Discuss the MSE values you
see and which model you prefer. Then fit the 'best' model to the entire data set.

We will run the function `cv_finder` to evaluate the different models, using the first 250 days solely as training data while the remaining days will be used as testing data so that we can calculate the total mean squared errors (MSE). First, we start with the SLR model, which uses the variable `CO(GT)` as its only predictor.

In [68]:
#SLR model: CO(GT) only, starting with day 250
#X is raw_air_quality[['CO(GT)'], y is raw_air_quality[['C6H6(GT)']]
cv_finder(raw_air_quality[['CO(GT)']], raw_air_quality[['C6H6(GT)']], 250)

69769.05327146314

Now we do the same for the MLR model, which uses the variables `CO(GT)`, `T`, `RH`, and `AH` as predictors.

In [69]:
#SLR model: CO(GT) only, starting with day 250
#X is raw_air_quality[['CO(GT)', 'T', 'RH', 'AH'], y is raw_air_quality[['C6H6(GT)']]
cv_finder(raw_air_quality[['CO(GT)', 'T', 'RH', 'AH']], raw_air_quality[['C6H6(GT)']], 250)

52159.942663933885

As we can see above, the MLR model has a lower total MSE than the SLR model does (52159.943 < 69769.053), which suggests that the MLR model is a better fit for our data.

Since we have chosen the MLR model as the better model, we can now fit it to the entire data set:

In [77]:
#Fit our predictors for the MLR model over the entire raw_air_quality[['C6H6(GT)']] set
mlr_X = raw_air_quality[['CO(GT)', 'T', 'RH', 'AH']]
mlr_y = raw_air_quality[['C6H6(GT)']]

mlr_best = LinearRegression().fit(mlr_X, mlr_y)

#See what intercepts and coeffecients are used in this model

print(mlr_best.intercept_)
print(list(zip(mlr_X.columns, mlr_best.coef_)))
print(mlr_X.columns)

[-2.32732844]
[('CO(GT)', array([ 4.80090314,  0.1030811 , -0.00847744,  0.97289547]))]
Index(['CO(GT)', 'T', 'RH', 'AH'], dtype='object')


Thus, our MLR model can be written as:

**C6H6(GT)** = -2.327 + 4.801**CO(GT)** + 0.103**T** - 0.008**RH** + 0.973**AH**